# NerfBusters!
## This notebook is used for creating Nerfacto models and further trying to reduce ghostly artifacts by utilizing the Nerfbusters model.
the relevant code used in this notebook is from: [ethanweber/nerfbusters](https://github.com/ethanweber/nerfbusters/tree/ethan/moving_data_location) 
 <br>Note! Using NerfBusters Utilizes a seperate branch of nerfstudio, so this notebook is used seperately from the NerfStudio.ipynb
 <br>You May Want to re-start the machine if you want to ensure that you are using the new specified Nerfstudio branch, or you could checkout the nerfbusters-changes branch

## Setting Up the Environment
Note: this code is made to work seamelessly with a paperspace notebook, by instlling all the relevant dependencies, You may want to change the location you are cloning the code to depending on your needs.


In [ ]:
#Run this when you are wanting to run NerfBusters
!pip install --upgrade --user pip
!pip uninstall torch torchvision functorch tinycudann -y
!pip uninstall torchaudio -y
!pip install --upgrade --user jax jaxlib
#!pip install --user torch==2.0.1+cu118 torchvision==0.15.2+cu118 --extra-index-url https://download.pytorch.org/whl/cu118
#!pip install torch==1.12.1+cu113 torchvision==0.13.1+cu113 -f https://download.pytorch.org/whl/torch_stable.html
!pip install torch==1.13.1 torchvision functorch --extra-index-url https://download.pytorch.org/whl/cu117
#!pip install torchaudio
!pip install -U flax
!pip install --upgrade --user tensorflow
!pip install typing-extensions #==3.10.0

#!pip install --user torchaudio==2.0.2+cu118 -f https://download.pytorch.org/whl/torch_stable.html
#!gdown "https://drive.google.com/u/1/uc?id=1-7x7qQfB7bIw2zV4Lr6-yhvMpjXC84Q5&confirm=t"
#!pip install tinycudann-1.7-cp310-cp310-linux_x86_64.whl
!pip install --user ninja git+https://github.com/NVlabs/tiny-cuda-nn/#subdirectory=bindings/torch
!pip install --user git+https://github.com/NVlabs/tiny-cuda-nn/#subdirectory=bindings/torch
#!pip install --upgrade --user nerfstudio

%cd /
%cd notebooks
#!pip install git+https://github.com/nerfstudio-project/nerfstudio.git@nerfbusters-changes
#!git clone --branch nerfbusters-changes  --single-branch https://github.com/nerfstudio-project/nerfstudio.git
%cd nerfstudio
!pip install --upgrade pip setuptools
!pip install -e .

%cd ..

#!git clone https://github.com/ethanweber/nerfbusters.git
%cd nerfbusters
!pip install -e .

!pip install protobuf==3.20.0

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 83.5 MB/s eta 0:00:00
Found existing installation: torch 1.12.1+cu116
Uninstalling torch-1.12.1+cu116:


## If Installing from scratch import relevant binvox to voxelize cubes & pretrained Diffusion Model

In [ ]:
%mkdir bins
%cd bins
!wget -O binvox https://www.patrickmin.com/binvox/linux64/binvox?rnd=16811490753710
%cd ../
!chmod +x bins/binvox
!python nerfbusters/download_nerfbusters_dataset.py diffusion-cube-weights

## Trying to use the viewer

In [3]:
#%cd /content

# Install localtunnel
# We are using localtunnel https://github.com/localtunnel/localtunnel but ngrok could also be used
!npm install -g localtunnel

# Tunnel port 7007, the default for
!rm url.txt 2> /dev/null
get_ipython().system_raw('lt --port 7007 >> url.txt 2>&1 &')

import time
time.sleep(3) # the previous command needs time to write to url.txt


with open('url.txt') as f:
  lines = f.readlines()
websocket_url = lines[0].split(": ")[1].strip().replace("https", "wss")
# from nerfstudio.utils.io import load_from_json
# from pathlib import Path
# json_filename = "nerfstudio/nerfstudio/viewer/app/package.json"
# version = load_from_json(Path(json_filename))["version"]
url = f"https://viewer.nerf.studio/?websocket_url={websocket_url}"
print(url)
print("You may need to click Refresh Page after you start training!")
from IPython import display
display.IFrame(src=url, height=800, width="100%")

m#################⠂) ⠦ reify:yargs-parser: http fetch GET 200 https://registry.
added 22 packages, and audited 23 packages in 2s

3 packages are looking for funding
  run `npm fund` for details

found 0 vulnerabilities
npm notice 
npm notice New major version of npm available! 8.19.3 -> 10.2.0
npm notice Changelog: https://github.com/npm/cli/releases/tag/v10.2.0
npm notice Run npm install -g npm@10.2.0 to update!
npm notice 
https://viewer.nerf.studio/?websocket_url=wss://silver-geese-cheat.loca.lt
You may need to click Refresh Page after you start training!


## Training Initial Nerfacto Model

In [ ]:
#!ns-train vanilla-nerf --data content/data/nerfstudio/custom2
!ns-train nerfacto --data /notebooks/content/data/nerfstudio/cropped2  --vis viewer
#!ns-train nerfacto --data /notebooks/content/data/nerfstudio/custom2/transforms.json
#!ns-train instant-ngp --data content/data/nerfstudio/custom2

[22:04:50] Using --data alias for --data.pipeline.datamanager.data                                          ]8;id=730836;file:///notebooks/nerfstudio/scripts/train.py\train.py]8;;\:]8;id=45675;file:///notebooks/nerfstudio/scripts/train.py#222\222]8;;\
──────────────────────────────────────────────────────── Config ────────────────────────────────────────────────────────
TrainerConfig(
    _target=<class 'nerfstudio.engine.trainer.Trainer'>,
    output_dir=PosixPath('outputs'),
    method_name='nerfacto',
    experiment_name=None,
    project_name='nerfstudio-project',
    timestamp='2023-10-16_220450',
    machine=MachineConfig(seed=42, num_gpus=1, num_machines=1, machine_rank=0, dist_url='auto'),
    logging=LoggingConfig(
        relative_log_dir=PosixPath('.'),
        steps_per_log=10,
        max_buffer_size=20,
        local_writer=LocalWriterConfig(
            _target=<class 'nerfstudio.utils.writer.LocalWriter'>,
            enable=True,
            stats_to_track=(
  

## Training NerfBusters on Nerfacto Model

In [1]:
#ns-train nerfbusters --data /notebooks/content/data/nerfstudio/custom2 --pipeline.nerf-checkpoint-path $NERF_CHECKPOINT_PATH nerfstudio-data --eval-mode train-split-fraction
!ns-train nerfbusters --data /notebooks/content/data/nerfstudio/cropped2 --pipeline.nerf-checkpoint-path /notebooks/nerfbusters/outputs/cropped2/nerfacto/2023-10-14_185208/nerfstudio_models/step-000029999.ckpt nerfstudio-data --eval-mode train-split-fraction
#!ns-train nerfbusters --data /notebooks/content/data/nerfstudio/custom2 --pipeline.nerf-checkpoint-path /notebooks/outputs/cropped2/nerfacto/version1/nerfstudio_models/step-000029999.ckpt nerfstudio-data --eval-mode train-split-fraction

[12:14:55] Using --data alias for --data.pipeline.datamanager.data                                          ]8;id=707516;file:///notebooks/nerfstudio/scripts/train.py\train.py]8;;\:]8;id=186763;file:///notebooks/nerfstudio/scripts/train.py#222\222]8;;\
──────────────────────────────────────────────────────── Config ────────────────────────────────────────────────────────
TrainerConfig(
    _target=<class 'nerfstudio.engine.trainer.Trainer'>,
    output_dir=PosixPath('outputs'),
    method_name='nerfbusters',
    experiment_name=None,
    project_name='nerfbusters-project',
    timestamp='2023-10-15_121455',
    machine=MachineConfig(seed=42, num_gpus=1, num_machines=1, machine_rank=0, dist_url='auto'),
    logging=LoggingConfig(
        relative_log_dir=PosixPath('.'),
        steps_per_log=10,
        max_buffer_size=20,
        local_writer=LocalWriterConfig(
            _target=<class 'nerfstudio.utils.writer.LocalWriter'>,
            enable=True,
            stats_to_track

## Render Video from which frames can be extracted

In [3]:
!export PathToCamera=/notebooks/custom-camera-paths/nerfbusters_camera_path.json
!export PathToYML=/notebooks/nerfbusters/outputs/cropped2/nerfbusters/2023-10-15_002302/config.yml
!export OutputFileName=/notebooks/renders/cropped2/renderBustersAttempt.mp4
#!ns-render camera-path --load-config outputs/custom2/nerfacto/2023-09-27_020244/config.yml --camera-path-filename content/data/nerfstudio/custom2/camera_paths/camera_path.json --output-path renders/custom2/testing.mp4
#!ns-render camera-path --load-config outputs/cropped2/nerfacto/2023-09-28_215420/config.yml --camera-path-filename content/data/nerfstudio/cropped2/camera_paths/2023-09-28_195259.json --output-path renders/cropped2/cropped-every.mp4
#!ns-render camera-path --load-config outputs/custom2/nerfacto/2023-10-14_115723/config.yml --camera-path-filename /notebooks/content/data/nerfstudio/custom2/camera_paths/2023-10-14_115723.json --output-path renders/custom2/2023-10-14_115723.mp4
!ns-render --load-config /notebooks/nerfbusters/outputs/cropped2/nerfbusters/2023-10-15_002302/config.yml --camera-path-filename /notebooks/custom-camera-paths/nerfbusters_camera_path.json --output-path /notebooks/renders/cropped2/renderBustersAttempt.mp4
#!ns-render --load-config /notebooks/nerfbusters/outputs/cropped2/nerfacto/2023-10-14_152606/config.yml --camera-path-filename /notebooks/content/data/nerfstudio/cropped2/camera_paths/2023-10-14_121551.json --output-path renders/cropped2/renderBustersBefore.mp4
#!ns-render camera-path --load-config outputs/custom2/nerfacto/2023-09-27_020244/config.yml --camera-path-filename content/data/nerfstudio/custom2/camera_paths/camera_path.json --output-path renders/custom2/testing.mp4
#!ns-render camera-path --load-config /notebooks/outputs/cropped2/nerfacto/2023-09-28_215420/config.yml --camera-path-filename custom-camera-paths/TwentySecondPath.json --output-path renders/cropped2/renderBustersBeforeRefined.mp4
#!ns-render camera-path --load-config outputs/custom2/nerfacto/2023-09-28_144853/config.yml --camera-path-filename content/data/nerfstudio/cropped2/camera_paths/2023-09-28_195259.json --output-path renders/custom2/testing.mp4
#!ns-render camera-path --load-config outputs/custom2/nerfacto/2023-09-27_020244/config.yml --camera-path-filename content/data/nerfstudio/custom2/camera_paths/2023-09-27_020244.json --output-path renders/custom2/2023-09-27_020244.mp4

[12:56:23] Auto image downscale factor of 1                                                 ]8;id=230417;file:///notebooks/nerfstudio/nerfstudio/data/dataparsers/nerfstudio_dataparser.py\nerfstudio_dataparser.py]8;;\:]8;id=833631;file:///notebooks/nerfstudio/nerfstudio/data/dataparsers/nerfstudio_dataparser.py#402\402]8;;\
[12:56:24] Skipping 0 files in dataset split train.                                         ]8;id=900543;file:///notebooks/nerfstudio/nerfstudio/data/dataparsers/nerfstudio_dataparser.py\nerfstudio_dataparser.py]8;;\:]8;id=788322;file:///notebooks/nerfstudio/nerfstudio/data/dataparsers/nerfstudio_dataparser.py#186\186]8;;\
           Skipping 0 files in dataset split test.                                          ]8;id=518588;file:///notebooks/nerfstudio/nerfstudio/data/dataparsers/nerfstudio_dataparser.py\nerfstudio_dataparser.py]8;;\:]8;id=292213;file:///notebooks/nerfstudio/nerfstudio/data/dataparsers/nerfstudio_dataparser.py#186\186]8;;\
S